# **Lesson 6 - Peptide Quantitation**

In this lesson, we'll learn about how we can quantify a peptide in our sample. Like **Lesson 5**, this lesson is a core part of data analysis. Bioinformatics researchers have made significant contributions to methods for quantitation.

## **Assumptions**

It is assumed that the reader has completed the prior lessons and is familiar with biology and introductory chemistry. This lesson expands on concepts from [Lesson 1](https://colab.research.google.com/drive/1sDMcPdqfggWA1vrD4Odtruw_0owKnIMy?usp=sharing) and [Lesson 3](https://colab.research.google.com/drive/1SvigFgC8POvbZAHoMMW5u2XQLjw11_sm?usp=sharing), specifically intensity and chromatography. It is assumed that you are comfortable with liquid chromatography and an XIC as presented in Lesson 3. Please review Lesson 3 if you need a refresher.

## **Goals**

At the end of this lesson, you should be able to:

- Understand how measured intensity is related to quantitation.
- Analyze MS1 data to define LC peaks.
- Compare different quantitation methods and identify strengths and weaknesses to the various methods.

## **Context**

In **Lesson 1**, we first encountered a spectrum and discussed briefly that the y-axis represents intensity. In **Lesson 3**, we discussed liquid chromatography (LC) and described how this introduces a time element to our experiment. Now an experiment acquires many spectra, perhaps 20 spectra every second for up to an hour. Importantly, we learned that a peptide elutes over a short time period. This was graphically demonstrated by comparing the intensity of a peptide over several adjacent spectra. Plotting this measurement over time is called an extracted ion chromatogram, or XIC.

The ultimate goal of proteomics is to measure a sample and give a quantitative catalog of the peptides/proteins - i.e., how much of each peptide is in the sample. In [Lesson 5](https://colab.research.google.com/drive/1Weihp1oRIgiXaKwulyeGAcSAuUjb9ihl?usp=sharing), we discussed how to identify peptides. The purpose of this lesson is to take the last step and quantify peptides.

## **Using this Tutorial**

This tutorial is designed to be interactive, and you are encouraged to change the code and explore. To do this, you'll need to save a copy of this so that you have editing permissions. Use `File->Save a copy in Drive` to make an editable copy for yourself. Colab notebooks consist of text cells (like this one) and code cells. You interact with the notebook by executing (running) the code cells by clicking the "play button" in each cell. You can also run all cells at once by using `Runtime->Run all`.

---

## **Part 1. Installation and Setup**

Before diving into the practical aspects of peptide quantitation, let's prepare our environment by installing the necessary Python packages and defining the necessary functions. These packages will enable us to analyze and visualize MS data effectively. To apply the concepts we've learned, we'll be working with real MS data, so we'll be loading the data files into the Colab environment using `gdown`.

In this notebook, some code cells have been 'hidden' for brevity. You can recognize these because they have just a play button and a small text prompt `Show code`. In addition to the setup code, these include code that we will use throughout the lesson - some functions from previous lessons, some plotting code, and code to find peak boundaries. You may want to look at this later in the lesson, but for now you can probably just click through. The first task is to establish the basic ideas behind **measuring quantity**.

In [ ]:
# @title Run this cell to set up the coding environment, including installing and loading necessary Python packages and loading in the data files.
%%capture

!pip install gdown
!pip install pyteomics==4.6.1
!pip install plotly==5.18.0
!pip install pandas
!pip install spectrum_utils==0.4.2
!pip install numpy


import pyteomics
from pyteomics import mzml, auxiliary
import gdown
import plotly.io as pio
import plotly.tools as tls
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import pandas as pd
import numpy as np
import random
import spectrum_utils.plot as sup
import spectrum_utils.spectrum as sus
import matplotlib.pyplot as plt
import seaborn as sns
from decimal import Decimal

pd.set_option('display.max_columns', 500)

## Files from Lesson 5
!gdown 1LnRmVxOHxKZt_oeyrcuTnlfy-Asf4AUr
mzml_path = '/content/20150708_QE3_UPLC8_DBJ_SA_Hela_39frac_Trypsin_21.mzML'

!gdown 1yNeczYxNKYeNwiEqR3yMZSbFb7xNbbrk
psm_path = '/content/20150708_QE3_UPLC8_DBJ_SA_Hela_39frac_Trypsin_21_psm_with_decoys.tsv'

# LC-MS file from Lesson 3
!gdown 1U6EoLTCcqAHwnCv_we4vGCcOBs_yNujt
lc_mzml_path = "/content/04-17-23_CA_Tryp_MS1_10min.mzML"

In [ ]:
# @title Run this cell to declare a function that gets a spectrum object (from Lesson 1).
def get_spectrum_object(mzml_path, scanNum):
  mzml = pyteomics.mzml.MzML(mzml_path)
  my_id = 'controllerType=0 controllerNumber=1 scan='+ str(scanNum)
  spectrum = mzml.get_by_id(my_id)
  return spectrum

In [ ]:
# @title Run this cell to declare a function that gets the retention time for a spectrum (from Lesson 3).
# `spectrum` should be a spectrum object generated in get_spectrum_object
def get_retention_time(spectrum):
    return spectrum['scanList']['scan'][0]['scan start time']

In [ ]:
# @title Run this cell to declare a function that plots multiple MS1 scans as subplots for easier viewing and comparison (from Lesson 3).

# Because we will be showing multiple spectra, I will use a modified plot function
# to make viewing easier
def subplot(x_min=None, x_max=None, title=None, scans=None, num_cols=None, mzml_path=None):
    axis_style = dict(
        linecolor='black',
        showgrid=False,  # This will remove gridlines
        zerolinecolor='gray'
    )

    # This lets us either input a list of scans or a range of scans
    if isinstance(scans, tuple) and len(scans) == 2:
        scan_nums = list(range(scans[0], scans[1] + 1))
    elif isinstance(scans, list):
        scan_nums = scans

    # Format rows/columns
    num_scans = len(scan_nums)
    num_rows = -(-num_scans // num_cols)

    max_intensity = 0
    subplot_titles = []
    for scan_num in scan_nums:
        spec = get_spectrum_object(mzml_path, scan_num)
        current_max = max(spec['intensity array'])
        max_intensity = max(max_intensity, current_max)

        subplot_titles.append(f"RT: {get_retention_time(spec):.2f} min")

    fig = make_subplots(rows=num_rows, cols=num_cols, subplot_titles=subplot_titles, vertical_spacing=0.1)

    for idx, scan_num in enumerate(scan_nums):
        spectrum = get_spectrum_object(mzml_path, scan_num)
        X = spectrum['m/z array']
        Y = spectrum['intensity array']
        trace = go.Scatter(x=X, y=Y, mode='lines', name='Spectrum',
                           showlegend=False, line=dict(color='black'))

        row = idx // num_cols + 1
        col = idx % num_cols + 1
        fig.add_trace(trace, row=row, col=col)
        fig.update_xaxes(title_text="m/z", range=[x_min, x_max], **axis_style, row=row, col=col)

        yaxis_title = "Intensity (ppm)" if col == 1 else None
        show_yaxis_ticks = True if col == 1 else False
        fig.update_yaxes(title_text=yaxis_title, range=[0, max_intensity], showticklabels=show_yaxis_ticks,
                         tickformat=".1e", **axis_style, row=row, col=col)

    fig.update_layout(plot_bgcolor='white', paper_bgcolor='white')
    fig.update_layout(title_text=title)
    fig.show()

In [ ]:
# @title Run this cell to declare functions that plot an XIC (from Lesson 3).

# This makes the xic more readable
def clean_values(df):
    df_slim = df.sort_values('intensity')
    df_slim = df_slim.drop_duplicates(subset=["scan"], keep="last")
    df_slim = df_slim.sort_values('time')
    return df_slim

# Searching through all of our data from MS1 scans that have a mz score in a
#  specific range, and then keeping track of the intensity of the scan that found
#   that mz score, along with the time that it was found at.
def get_MS1_values(target_mz, peak_time, data, window = None):
    df = pd.DataFrame(columns=['scan', 'time', 'intensity', "mz"])
    tol = 0.1
    mz_min = target_mz - tol
    mz_max = target_mz + tol
    if not window : window = .05
    times = data.time[peak_time - window: peak_time + window]

    for spectra in times:
        # checking that we have an MS1 scan
        if spectra['ms level'] == 1:

            # getting the time
            time = (spectra['scanList']['scan'][0].get('scan start time'))

            # get scan number
            scanString = spectra['id']
            startSpot = scanString.find('scan=')
            scanNum = scanString[startSpot + 5:]

            # get intensity and mz
            intensity_array = spectra['intensity array']
            mz_array = spectra["m/z array"]

            # checking through all mz array for anything in our range of mz values
            for x in range(0, len(mz_array)):
                if mz_array[x] > mz_min and mz_array[x] < mz_max:
                    intensity = intensity_array[x]

                    # creating a new row and adding it into the df
                    row = {'scan': scanNum, 'time': time, 'intensity': intensity, 'mz': mz_array[x]}
                    # df = pd.concat([df, pd.DataFrame([row])], ignore_index=True)  # depreciated
                    df = (pd.DataFrame([row]) if df.empty else pd.concat([df, pd.DataFrame([row])], ignore_index=True))
    cleaned_df = clean_values(df)

    return cleaned_df

def make_xic(mz, time, mz_data, time_window = None):
    xic = get_MS1_values(mz, time, mz_data, window = time_window)

    axis_style = dict(
        linecolor='black',
        zerolinecolor='gray'
    )

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=xic['time'], y=xic['intensity'], mode='lines+markers', line=dict(color='black')))

    fig.update_layout(
        title=f'XIC for mz {mz} across time',
        xaxis_title='Retention Time (min)',
        yaxis_title='Intensity',
        xaxis=axis_style,
        yaxis=axis_style,
        plot_bgcolor='white',
        paper_bgcolor='white'
    )

    fig.show()

## **Part 2. Measuring Quantity**

Let's start with the heart of the issue - what are we measuring? If you imagine a cell, such as you've seen in elementary biology classes, it is packed full of protein components busy doing their job keeping a cell alive. Let's focus on just one protein, a protein named *rpl24*. This protein is one of the parts of a ribosome, the pepper-like dots that you see in a cartoon of a cell (see figure below). Ribosomes are the cell factories responsible for making new proteins. In proteomics, we want to identify and quantify all the proteins in our sample, proteins like *rpl24*. In a healthy cell, there will be lots or *rpl24*, but in some diseases like ALS, there are only a few ribosomes. The cells are sick. So the quantity we measure of *rpl24* should be less.

<figure>
<img src="https://drive.google.com/uc?export=view&id=1-GAhsUI7BtcbUXB5kqk9mcu8V4JjNEeQ" width="500">
<figcaption>Made with BioRender.com</figcaption>
</figure>

In MS data, we measure quantity as the intensity of a peak in the spectrum. It's not an exact count of copies of a protein in a cell, but it's a good proxy. You'll remember from **Lesson 1** that ionization is a way to get peptides into the mass spectrometer, and we note here that not all peptides like to be ionized. Some peptides ionize more easily than others, so the intensity observed in the spectrum cannot be thought of as a true count from the sample. These and other gory chemistry details can be discussed in an analytical chemistry course. For our beginning tutorials, we'll say that intensity in the spectrum serves as a good proxy for quantity in the sample. (If you get stuck next to an analytical chemist in an airport, they could talk your ear off about this, but we'll just stick with this much for now.)

## **Part 3. The Chromatography Complication**

As you'll remember from **Lesson 3**, the MS data of a complex sample has many thousands of proteins and millions of peptides. To help simplify the measurements in a spectrum, we introduced liquid chromatography, or LC. LC-MS data contains many spectra measured over time as peptides elute (solubilize) and flow into the mass spectrometer. We can trace a single peptide's elution by watching its intensity in a few adjacent spectra. Here we repeat the code from **Lesson 3** for a group of MS spectra:

In [ ]:
# This function is defined above in Part 1 - take a look at the code up
#   there to see what it is doing
subplot(x_min=1124, x_max=1134, scans = (2697,2706), num_cols = 5, mzml_path=lc_mzml_path)

Looking at this panel of ten spectra, we see a timeframe of 0.06 minutes (3-4 seconds). In the first panel, the intensity of our peptide is very low. It gradually increases in intensity, peaks and then declines.

In addition to this 'spectrum centric' view, we can make a 'time centric' view to more easily see a peptide's elution. Above we have a set of spectra plotting m/z vs. intensity. The extracted ion chromatogram, or XIC, plots only one m/z and uses time and intensity as its axes. Here we repeat the code from **Lesson 3** to create an XIC:

In [ ]:
# Choose the mz and retention time (in minutes) that you would like to draw an XIC for
mz = 1127.5916
time = 16.74
lc_mzml = pyteomics.mzml.MzML(lc_mzml_path)

# This function is defined above in Part 1 - take a look at the code up
#   there to see what it is doing
make_xic(mz, time, lc_mzml)

At 10 points in time, we have a measurement for m/z = 1127.5916 forming a shape like a bell-curve. This is a beautiful **LC peak**. Now let's take a moment in the code cells below and look at the LC peaks for other peptides. To do this, we will get the psm file from **Lesson 5** and note the m/z and retention time of a peptide. Then we will use the code from above to make XICs for the peptides.

For this exercise, let's take a look at several peptides, including `INMNGVNSSNGVVDPR`. You'll notice that I've only written the code to look at `INMNGVNSSNGVVDPR`, you will need to write the code to look at additional peptides yourself.

In [ ]:
psm = pd.read_csv(psm_path, sep='\t')
mzml = pyteomics.mzml.MzML(mzml_path)

In [ ]:
mz = psm[(psm['Peptide'] == "INMNGVNSSNGVVDPR") & (pd.isna(psm['Modified Peptide']))]['Observed M/Z'].tolist()[0]

# divide by 60 to put time in minutes
time = psm[(psm['Peptide'] == "INMNGVNSSNGVVDPR") & (pd.isna(psm['Modified Peptide']))]['Retention'].tolist()[0] / 60

make_xic(mz, time, mzml, 0.5)

Go ahead and take a moment to explore some other peaks. You will need to get the mz and time variables used in the plotting above by searching through the `psm` variable from **Lesson 5**.

Looking at different spectra can be enlightening as you see variability. In the XIC for `INMNGVNSSNGVVDPR`, you may notice that it has many more points across the LC peak, because it elutes over a much longer period of time (~ 0.4 minutes). What unique aspects of an LC peak do you see in the examples that you plotted?

In [ ]:
## space for you to plot XICs of other peptides.

#mz =
#time =
#make_xic(mz, time, mzml, 0.5)

## **Part 4. Defining an LC Peak**

LC complicates measuring quantity. We need to sum up all the intensities over time. How do we define where to start and stop our summing? Or in the MS vernacular, 'what are our **peak boundaries**?' In some of the LC peaks you viewed above, boundary definition is not hard. There is a spectrum where m/z = 1127.59 has zero intensity and the next spectrum has some intensity. This defines the start, and a mirrored situation defines the stop. There is nothing else within our viewing window, so it's a pretty easy example.

What happens if there are two things in our XIC? Do we think these came from two different peptides with the same m/z? That is a possibility. Remember that the reason for using LC in our experiment is precisely because multiple peptides have the same m/z. So in reporting intensity, we have to correctly assign the abundance to the right peptide.

Let's first look at an example where there are two different LC peaks, cleanly separated by some time measuring near the baseline.

In [ ]:
mz = 612.3583
time = 12.5

make_xic(mz, time, mzml, 0.5)

But what happens if the time between peaks is shorter? Or if there are fewer measurements defining a peak? Let's look at a hard example.

In [ ]:
peptide_sequence = 'TKGPLKQK'  # not needed for plotting, simply for your information
mz = 450.2877
time = 316.9380 / 60

make_xic(mz, time, mzml, 0.5)

The XIC for peptide `TKGPLKQK` has some very strange behavior. It has three spikes in intensity. There are only a few measurements at low intensity and then things jump back up to the full intensity. Are these all one peak, or perhaps two or three peaks? Note that the y-axis is much lower in intensity than our easy examples. At low intensity, measurements in the mass spectrometer can be sensitive to noise, mis-measurement, or other challenges in chemistry.  The PSM associated with this XIC was taken at minute 5.28, and so it was acquired during the middle peak.  Our middle peak is separated by only a very short time from its neighboring peaks. What gets summed into an abundance measurement for this peptide? If we decide it is all one peak, do we use the low-intensity measurements as is? or do we smooth them over and impute what we believe the measurement should be?

For a second hard example, let's look at the XIC for peptide `QPVGGGQK`.

In [ ]:
peptide_sequence = 'QPVGGGQK'  # not needed for plotting, simply for your information
mz = 385.7115
time = 319.0129 / 60

make_xic(mz, time, mzml, 0.5)

In the region of interest there is a beginning spike of intensity in a single measurement. Intensity on the y-axis is in the millions, so not a 'low intensity' measurement. But it is still unexpected to have this single spike. Does this get included in our summed intensity? As a second oddity, even if we ignore the beginning spike , this does not have a nice gaussian shape, but rather a very asymmetric shape. What gets summed up into the reported abundance for this peptide?

So, what do we do? How do we report an intensity in these difficult cases? In each of these scenarios, the data does not look like we expected. Depending on specific algorithmic implementations for peak boundary detection, the quantity reported for this peptide could have significant variability.

Some tools approach peak boundary detection with simple heuristics, and there are situations where these will and won't work. Historically, defining peak boundaries is most accurately approached through the classic computer science discipline of signal processing. This employs computational models for describing both the peak and the baseline (absence of a peak). In traditional signal processing, a variety of smoothing and convolution methods use the 1st and 2nd order derivatives of the XIC to define the boundaries. More modern signal processing is taking advantage of machine learning to understand what the signal should look like and what learned principles for declaring the boundary are. Both of these methods are a bit too involved for this tutorial, but it is important to appreciate the computational challenge involved.

## **Part 5. Summing Intensity of an LC Peak**

Once peak boundaries have been set, the final task is to sum the intensities and report a single quantitative value for the m/z, or peptide. The most common method is to simply sum peaks in the included MS1 spectra.

Let's go back to our **Lesson 3** example from **Part 3**. First, let's remind ourselves of what our spectra looked like:

In [ ]:
subplot(x_min=1124, x_max=1134, scans = (2697,2706), num_cols = 5, mzml_path=lc_mzml_path)

You'll notice that there are several peaks we could choose to sum up from the isotopic envelope (including the option of summing every peak included in the envelope across time). For simplicity in this example, let's sum up the peak we used to create the corresponding XIC for our quantitation (m/z = `1127.5916`):

In [ ]:
scans = (2697,2706)
mz_to_sum = 1127.5916

quant_value = 0
for scan_num in range(scans[0], scans[1] + 1):
  spectrum = get_spectrum_object(lc_mzml_path, scan_num)

  mz_values = spectrum['m/z array']
  intensity_values = spectrum['intensity array']

  for i, mz in enumerate(mz_values):
    if round(mz, 2) == round(mz_to_sum, 2):
      quant_value += intensity_values[i]

print('%.2E' % Decimal(str(quant_value)))

1.41E+11


Other variations of summing intensities:

1. Using all peaks in the isotopic envelope (more complex but more accurate).

2. Using smoothed instead of raw signal. As you saw in the hard examples above, some LC peaks are not really smooth - and this complicates the peak boundary detection. Therefore, several software programs first smooth the XIC prior to peak detection and also use this smoothed data in the summation. Many different smoothing kernels exist, but a simple sliding window smoothing with a 3 scan window looks like:

$$intensity_{i_{new}} = mean(intensity_{i-1},\space{}intensity_i,\space{}intensity_{i+1})$$

3. Using the apex only. A different way to deal with the challenges posed by rough peaks is to simply choose the peak apex as the quantitative value. This method does not sum at all.

There are many other methods for quantification beyond the ones discussed above, and there is a reasonably vigorous scientific debate about which does best - complete with a bake-off and benchmark datasets. If this is of interest, you can check it out [here](https://www.nature.com/articles/s41597-022-01216-6) and [here](https://www.nature.com/articles/nbt.3685).

## **Part 6. Linking Identification and Quantitation**

Finally, we come to the last part. The careful observer will have noticed that **Lessons 3 and 6** talked about *MS data* used in quantification. **Lessons 4 and 5** talked about *MS/MS data* used in identification. This is not a typo. We gather identification and quantitation values from different parts of our data. Now, the task is to join the two so that we have a simple table noting both a peptide identity in one column and the peptide quantity in another column.

Using the data from **Lesson 5**, we're going to make the XIC for peptide `LMEAMSEVKA`, which was found in MS/MS spectrum number `25278`. Let's use a generous range and search the retention time (38.56) +/- 30 seconds.

In [ ]:
mz = psm[psm['Spectrum'].str.contains('.25278.25278.')]['Observed M/Z'].tolist()[0]
time = psm[psm['Spectrum'].str.contains('.25278.25278.')]['Retention'].tolist()[0] / 60

make_xic(mz, time, mzml, 0.5)

It is important to remember about the interleaving of MS and MS/MS spectra from [Lesson 4](https://colab.research.google.com/drive/13WEV58HpkY7f0kFi2BA5ia5p0XZCL3Cq?usp=sharing). The LC peak for this peptide ranges from **38.515-38.634** minutes. The spectrum numbers associated with these 9 measurements are: `25237`-`25354` (see code below). You see where our MS/MS spectrum fits in there? It was `25278`. The MS/MS spectrum was acquired during the elution of our peptide as seen in the XIC.

In [ ]:
# This function is defined above in Part 1 - take a look at the code up
#   there to see what it is doing
MS1_scans = get_MS1_values(mz, time, mzml, 0.5)
MS1_scans[(round(MS1_scans['time'], 3) >= 38.515) & (round(MS1_scans['time'], 3) <= 38.634)].reset_index()

index   scan       time     intensity          mz
0     27  25237  38.514999  3.149657e+05  554.775269
1     28  25257  38.533799  3.226922e+06  554.771606
2     29  25272  38.548937  1.086965e+07  554.771790
3     30  25288  38.564599  2.214122e+07  554.771851
4     31  25300  38.577643  2.899651e+07  554.771912
5     32  25303  38.583857  2.959133e+07  554.771973
6     33  25321  38.601487  1.511109e+07  554.772034
7     34  25338  38.617945  4.726295e+06  554.771118
8     35  25354  38.633576  2.685394e+05  554.772705

The common intermediate output of quantitation is a list of LC peaks and their spectrum ranges, intensities, and m/z values. The common intermediate output of identification is the spectrum number, peptide sequence, m/z, and various PSM scoring features. Thus, we combine these two outputs to form a final quantitative output - joining on spectrum number and m/z.

## **Conclusion**

The goal of this lesson was to describe how we calculate a quantity for a peptide ion in a proteomics dataset. We used MS1 spectra to define an ion's LC peak and then summed values from the included spectra to get a single number. That number is linked to a peptide identity by looking at the PSM identifications and finding the matching m/z and retention time.

## **Lesson 6 Terms**

* **LC peak**: the retention times and intensities for a specific m/z value within its boundaries
* **peak boundaries**: the start and stop of an *LC peak*